In [1]:
from openai import OpenAI
import datasets
import datetime
import re
import contextlib
import io
import termcolor

In [2]:
client = OpenAI(
    base_url="http://localhost:8000/v1",
    api_key="a.guha@northeastern.edu:77wlaJxIMpzvkt61S8Xi")

In [3]:
resp = client.chat.completions.create(
    model="llama3p3-70b-instruct",
    messages=[{"role": "user", "content": "Hello, world!"}],
    temperature=0,
)
resp.choices[0].message.content

"Hello! It's nice to meet you. Is there something I can help you with or would you like to chat?"

In [4]:
def extract_code_from_markdown(markdown_text: str):
    # Look for code blocks in the markdown text
    code_blocks = re.findall(r'```(?:python)?(.*?)```', markdown_text, re.DOTALL)
    
    # If no code blocks found, return empty string
    if not code_blocks:
        return None
    
    return code_blocks[0]


In [5]:
flights_data = datasets.load_dataset("nuprl/engineering-llm-systems", "flights", split="train")

In [6]:

# Transform the flights data to parse dates and times
flights = []
for flight in flights_data:
    flight = dict(flight)  # Convert to mutable dict
    # Parse date string to datetime.date
    flight['date'] = datetime.datetime.strptime(flight['date'], '%Y-%m-%d').date()
    # Parse times to datetime.time
    flight['departure_time'] = datetime.datetime.strptime(flight['departure_time'], '%H:%M').time()
    flight['arrival_time'] = datetime.datetime.strptime(flight['arrival_time'], '%H:%M').time()
    flights.append(flight)


def find_flights(origin: str, destination: str, departure_date: datetime.date) -> list[dict]:
    return [flight for flight in flights if flight['origin'] == origin and flight['destination'] == destination and flight['date'] == departure_date]

done_messages = [ ]

def done(message: str):
    done_messages.append(message)


### System Prompt

In [7]:
SYSTEM_PROMPT = """
You are an airline chatbot. Only answer airline queries. We have defined a function called

```python
def find_flights(origin: str, destination: str, departure_date: datetime.date) -> list[dict]:
```

It takes the origin and destination airport codes. And produces a list of dictionaries
containing flight information. Stuff like this:

```
{ 'id': 407,
  'date': datetime.date(2023, 1, 6),
  'airline': 'Delta',
  'flight_number': 'DL9926',
  'origin': 'ORD',
  'destination': 'JFK',
  'departure_time': datetime.time(20, 55),
  'arrival_time': datetime.time(22, 55),
  'available_seats': 172}
```
Use the find_flight functions to search for all flights.

Call the done function exactly once with what you want to say to the user.
Format the string argument to done nicely. Don't import anything and
don't define helpers. 
"""

ACTION_11 = """This code will find the flights you asked for:

```python
print(find_flights("BOS", "SFO", datetime.date(2023, 1, 6)))
```"""

OBS_1 = """I ran that code and got:

```
[]
```
"""

ACTION_12 = """
```python
done("Sorry, there are no flights available on that day from BOS to SFO.")
```
"""

FEW_SHOT_EXAMPLE_2 = """This code will find the flights you asked for:

```python
print(find_flights("JFK", "LHR", datetime.date(2023, 1, 2)))
```"""

OBS_2 = """
I ran that code and got:

```python
[]
```
"""


FEW_SHOT_EXAMPLE_2 = """This code will find the flights you asked for:

```python
print(find_flights("JFK", "LHR", datetime.date(2023, 2, 2)))
```"""

ACTION_22 = """
```python
done("I found a JetBlue flight that departs at 3:51pm (B69139)")
```
"""

OBS_3 = """
I ran that code and got:

```python
[{'id': 2, 'date': datetime.date(2023, 1, 3), 'airline': 'JetBlue', 'flight_number': 'B69139', 'origin': 'JFK', 'destination': 'LHR', 'departure_time': datetime.time(3, 51), 'arrival_time': datetime.time(5, 51), 'available_seats': 107}]
```
"""

ACTION_23 = """
```python
done("I found a JetBlue flight that departs at 3:51pm (B69139)")
```
"""

PROMPT_PREFIX = [
    { "role": "system", "content": SYSTEM_PROMPT },
    # Example 1
    { "role": "user", "content": "What flights are there from Boston to San Francisco on January 6, 2023? "},
    { "role": "assistant", "content": ACTION_11 },
    { "role": "user", "content": OBS_1 },
    { "role": "assistant", "content": ACTION_12 },
    # Example 2
    { "role": "user", "content": "How do I get to LHR from JFK on Jan 2 or Jan 3?" },
    { "role": "assistant", "content": FEW_SHOT_EXAMPLE_2 },
    { "role": "user", "content": OBS_2  },
    { "role": "assistant", "content": ACTION_22 },
    { "role": "user", "content": OBS_3  },
    { "role": "assistant", "content": ACTION_23 },
]


In [8]:
def run_query(messages: list):
    # print(messages)
    resp = client.chat.completions.create(
        model="llama3p3-70b-instruct",
        messages=messages,
        temperature=0.2,
    ).choices[0].message.content
    messages.append({"role": "assistant", "content": resp})
    # print(f"Response: {resp}")
    code = extract_code_from_markdown(resp)
    print(termcolor.colored(f"Code: {code}", "blue"))
    if code is None:
        return None
    with io.StringIO() as buf, contextlib.redirect_stdout(buf):    
        exec(code)
        output = buf.getvalue()
    print(termcolor.colored(f"Output: {output}", "green"))
    return output


In [9]:
def agent(user_query: str) -> str:
    done_messages.clear()
    messages = PROMPT_PREFIX + [{"role": "user", "content": user_query}]
    first_run = True
    while first_run or len(done_messages) == 0:
        first_run = False
        code_output = run_query(messages)
        messages.append({"role": "user", "content": f"I ran the following code and got:\n```\n{code_output}\n```"})

    print("\n".join(done_messages))


In [10]:
agent("What flights are there from la to atlanta on January 1st, 2023?")

Code: 
flights = find_flights("LAX", "ATL", datetime.date(2023, 1, 1))
if flights:
    message = "Here are the flights from LAX to ATL on January 1st, 2023: "
    for flight in flights:
        message += f"{flight['airline']} {flight['flight_number']} departing at {flight['departure_time']}, "
    done(message[:-2])  # remove the extra comma and space
else:
    done("Sorry, there are no flights available on that day from LAX to ATL.")

Output: 
Here are the flights from LAX to ATL on January 1st, 2023: JetBlue B69139 departing at 03:51:00, Southwest WN2445 departing at 08:08:00


In [11]:
agent("What flights are there from la to jfk on January 2nd, 2023?")

Code: 
flights = find_flights("LAX", "JFK", datetime.date(2023, 1, 2))
if flights:
    message = "Here are the flights from LAX to JFK on January 2nd, 2023: "
    for flight in flights:
        message += f"{flight['airline']} {flight['flight_number']} departing at {flight['departure_time']}, "
    done(message[:-2]) 
else:
    done("Sorry, there are no flights available on that day from LAX to JFK.")

Output: 
Here are the flights from LAX to JFK on January 2nd, 2023: Delta DL8261 departing at 20:59:00, Delta DL8777 departing at 21:06:00


In [12]:
agent("What flights are there from la to jfk on January 2st, 2023?")

Code: 
flights = find_flights("LAX", "JFK", datetime.date(2023, 1, 2))
if flights:
    result = "Flights from LAX to JFK on January 2, 2023: "
    for flight in flights:
        result += f"{flight['airline']} {flight['flight_number']} departing at {flight['departure_time']}, "
    done(result[:-2])
else:
    done("Sorry, there are no flights available on that day from LAX to JFK.")

Output: 
Flights from LAX to JFK on January 2, 2023: Delta DL8261 departing at 20:59:00, Delta DL8777 departing at 21:06:00


In [13]:
agent("What flights are there from la to jfk on January 1st or 2nd, 2023?")

Code: 
flights_jan1 = find_flights("LAX", "JFK", datetime.date(2023, 1, 1))
flights_jan2 = find_flights("LAX", "JFK", datetime.date(2023, 1, 2))
all_flights = flights_jan1 + flights_jan2
if all_flights:
    message = "Here are the flights from LAX to JFK on January 1st or 2nd, 2023: "
    for flight in all_flights:
        message += f"\n- {flight['airline']} {flight['flight_number']}: Departs {flight['departure_time']} on {flight['date']}"
    done(message)
else:
    done("Sorry, there are no flights available on those days from LAX to JFK.")

Output: 
Here are the flights from LAX to JFK on January 1st or 2nd, 2023: 
- Delta DL8261: Departs 20:59:00 on 2023-01-01
- Delta DL8261: Departs 20:59:00 on 2023-01-02
- Delta DL8777: Departs 21:06:00 on 2023-01-02


In [14]:
agent("What flights are there from la to jfk on January 1st or 2nd, 2023? I want the one that leaves earliest.")

Code: 
flights_jan1 = find_flights("LAX", "JFK", datetime.date(2023, 1, 1))
flights_jan2 = find_flights("LAX", "JFK", datetime.date(2023, 1, 2))
all_flights = flights_jan1 + flights_jan2
if all_flights:
    earliest_flight = min(all_flights, key=lambda x: x['departure_time'])
    done(f"The earliest flight from LAX to JFK is {earliest_flight['airline']} {earliest_flight['flight_number']} departing at {earliest_flight['departure_time']}.")
else:
    done("Sorry, there are no flights available on those days from LAX to JFK.")

Output: 
The earliest flight from LAX to JFK is Delta DL8261 departing at 20:59:00.


In [15]:
agent("Show me flights from la to jfk on Jan 1. But not Delta -- otherwise I'll do Jan 2.")

Code: 
flights = find_flights("LAX", "JFK", datetime.date(2023, 1, 1))
non_delta_flights = [flight for flight in flights if flight['airline'] != 'Delta']
if non_delta_flights:
    done("Here are the flights from LAX to JFK on Jan 1 that are not Delta: \n" + "\n".join([f"{flight['airline']} {flight['flight_number']} departs at {flight['departure_time']} " for flight in non_delta_flights]))
else:
    flights = find_flights("LAX", "JFK", datetime.date(2023, 1, 2))
    done("Here are the flights from LAX to JFK on Jan 2: \n" + "\n".join([f"{flight['airline']} {flight['flight_number']} departs at {flight['departure_time']} " for flight in flights]))

Output: 
Here are the flights from LAX to JFK on Jan 2: 
Delta DL8261 departs at 20:59:00 
Delta DL8777 departs at 21:06:00 


In [16]:
agent("Show me flights from la to jfk on Jan 1 or later in the week. Not Delta.")

Code: 
flights = find_flights("LAX", "JFK", datetime.date(2023, 1, 1))
flights += find_flights("LAX", "JFK", datetime.date(2023, 1, 2))
flights += find_flights("LAX", "JFK", datetime.date(2023, 1, 3))
flights += find_flights("LAX", "JFK", datetime.date(2023, 1, 4))
flights += find_flights("LAX", "JFK", datetime.date(2023, 1, 5))
flights += find_flights("LAX", "JFK", datetime.date(2023, 1, 6))
flights += find_flights("LAX", "JFK", datetime.date(2023, 1, 7))
non_delta_flights = [flight for flight in flights if flight['airline'] != 'Delta']
if non_delta_flights:
    message = "Here are the flights from LAX to JFK on Jan 1 or later in the week, excluding Delta: "
    for i, flight in enumerate(non_delta_flights):
        message += f"\nFlight {i+1}: {flight['airline']} {flight['flight_number']} on {flight['date']}"
    done(message)
else:
    done("Sorry, there are no flights available on that day from LAX to JFK, excluding Delta.")

Output: 
Here are the flights from LAX to JFK on Jan 1 o